In [6]:
!pip install dtale
!pip install geopandas

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 1.0 MB 2.8 MB/s 
     |████████████████████████████████| 6.3 MB 34.2 MB/s 
     |████████████████████████████████| 16.7 MB 421 kB/s 


In [7]:
import pandas as pd
import numpy as np
import plotly.express as px
from geopy.distance import geodesic as GD
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import scipy.stats
import folium
import dtale
import math
from pandas_profiling import ProfileReport
import geopandas as gpd
import matplotlib.pyplot as plt

In [8]:
school_enroll=pd.read_csv('https://raw.githubusercontent.com/IshjitSingh/DataDisca/IshjitSingh-visualisation/dv316-allschoolsFTEenrolmentsFeb2021.csv',sep=",",encoding='cp1252')
school_loc = pd.read_csv('https://raw.githubusercontent.com/IshjitSingh/DataDisca/IshjitSingh-visualisation/dv279-schoollocations2019.csv',sep=",",encoding='cp1252')

In [9]:
school_enroll['School_No'].unique
school_loc_dd=school_loc.drop_duplicates(subset=["School_No"])
school_loc_dd['School_No'].unique

<bound method Series.unique of 0          1
1          3
2          4
3          8
4         12
        ... 
2247    2220
2248    2221
2250    2223
2251    2224
2253    2226
Name: School_No, Length: 2112, dtype: int64>

In [10]:
merged_enroll= pd.merge(school_enroll,school_loc,on=["Education_Sector","Entity_Type","School_No","School_Name","School_Type"],how="left")

In [11]:
pd.set_option("display.max_columns", None)

In [12]:
merged_enroll
merged_enroll_es= merged_enroll.drop(columns=['Year','CENSUS_TYPE','Grand Total','Address_Line_1','Address_Line_2','Address_State','Postal_Address_Line_1','Postal_Address_Line_2','Postal_State','Full_Phone_No','LGA_ID',])

In [13]:
enroll_df=merged_enroll_es.melt(id_vars=["Education_Sector","Entity_Type","School_No","School_Name","School_Type","School_Status_x",'School_Status_y',"Address_Town","Address_Postcode","Postal_Town","Postal_Postcode","LGA_Name","X","Y"])

In [14]:
enroll_df.describe(include='all')

Education_Sector    Entity_Type      School_No       School_Name  \
count            106972  106972.000000  106972.000000            106972   
unique                3            NaN            NaN              2083   
top          Government            NaN            NaN  St Mary's School   
freq              72991            NaN            NaN              1692   
mean                NaN       1.317663    3500.229789               NaN   
std                 NaN       0.465570    2510.318708               NaN   
min                 NaN       1.000000       1.000000               NaN   
25%                 NaN       1.000000    1548.750000               NaN   
50%                 NaN       1.000000    2475.000000               NaN   
75%                 NaN       2.000000    5213.250000               NaN   
max                 NaN       2.000000    8916.000000               NaN   

       School_Type School_Status_x School_Status_y Address_Town  \
count       106972          106972          103917       103917   
unique           5               3               1         1298   
top        Primary               O               O    Frankston   
freq         74025          106784          103917          564   
mean           NaN             NaN             NaN          NaN   
std            NaN             NaN             NaN          NaN   
min            NaN             NaN             NaN          NaN   
25%            NaN             NaN             NaN          NaN   
50%            NaN             NaN             NaN          NaN   
75%            NaN             NaN             NaN          NaN   
max            NaN             NaN             NaN          NaN   

        Address_Postcode Postal_Town  Postal_Postcode          LGA_Name  \
count      103917.000000      103917    103917.000000            103917   
unique               NaN        1047              NaN                80   
top                  NaN    WERRIBEE              NaN  Yarra Ranges (S)   
freq                 NaN         752              NaN              3713   
mean         3369.851199         NaN      3371.259611               NaN   
std           303.918996         NaN       318.857180               NaN   
min          3000.000000         NaN      3000.000000               NaN   
25%          3123.000000         NaN      3122.000000               NaN   
50%          3225.000000         NaN      3225.000000               NaN   
75%          3638.000000         NaN      3638.000000               NaN   
max          3996.000000         NaN      8008.000000               NaN   

                    X              Y          variable          value  
count   103917.000000  103917.000000            106972  106972.000000  
unique            NaN            NaN                47            NaN  
top               NaN            NaN  Prep Males Total            NaN  
freq              NaN            NaN              2276            NaN  
mean       144.899689     -37.594835               NaN      28.443834  
std          1.072236       0.726257               NaN      92.636966  
min        141.082487     -38.753524               NaN       0.000000  
25%        144.661899     -37.969865               NaN       0.000000  
50%        145.035502     -37.798383               NaN       0.000000  
75%        145.259358     -37.586610               NaN      26.000000  
max        149.754296     -34.166857               NaN    3332.000000

In [15]:
enroll_df=enroll_df

enroll_df['Year']=""

In [16]:
enroll_df.to_csv('enroll_df.csv')

In [17]:
class_year=("Prep","1","2","3","4","5","6","7","8","9","10","11","12")

for x in class_year:
    mask=False
    mask = enroll_df['variable'].str.contains(x, na=False)
    enroll_df.loc[mask,'Year']=x

In [18]:
gender=("Male","Female")


In [19]:
for x in gender:
    mask=False
    mask = enroll_df['variable'].str.contains(x, na=False)
    enroll_df.loc[mask,'variable']=x

In [20]:
mask_1=True
mask_1 = ~enroll_df['variable'].str.contains("Total", na=False)
#for y in new_test.index:
   # if mask_1[y]:
    #    new_test.drop(labels=y,axis=0)

In [21]:
enroll_df=enroll_df.query('variable=="Male" or variable=="Female"')
enroll_df=enroll_df.dropna()
enroll_df['distance']=enroll_df.apply(lambda t: GD((t['Y'],t['X']),(-37.8110,144.9738)).km,axis=1)

dtype(mask)

In [22]:
px.scatter(enroll_df,x='distance',y='value',facet_col="variable",
           title="Male and Female Students with distance",
             labels={ # replaces default labels by column name
                "variable": "Student Gender",  "Year": "Class", "value": "Number of Students"
            },
            #category_orders={ # replaces default order by column name
             #   "day": ["Thur", "Fri", "Sat", "Sun"], "sex": ["Male", "Female"]
           # },
           # color_discrete_map={ # replaces default color mapping by value
           #     "Male": "RebeccaPurple", "Female": "MediumPurple"
            #},
            template="simple_white"
            )

In [23]:

enroll_df['distance_group']="Rest of Victoria"
enroll_df.loc[enroll_df['distance']<=30.0,'distance_group']="Melbourne and Surrounding Suburbs "
px.scatter(enroll_df,x='Year',y='value',facet_col='distance_group',color='variable')

In [24]:
grouped_df =enroll_df.groupby(by=["Year", "variable",'distance_group'], as_index=False).agg(
    {"value": "mean"}
)
#fig_dataset1=new_test_12.groupby(['variable']).sum('value')
fig = px.bar(grouped_df, x='Year', y='value',color="distance_group",barmode='group',
             title="Average Male and Female Students with location",
             labels={ # replaces default labels by column name
                "distance_group": "Location",  "Year": "Class", "value": "Number of Students","variable":"Student Gender"
            },
            #category_orders={ # replaces default order by column name
             #   "day": ["Thur", "Fri", "Sat", "Sun"], "sex": ["Male", "Female"]
           # },
           # color_discrete_map={ # replaces default color mapping by value
           #     "Male": "RebeccaPurple", "Female": "MediumPurple"
            #},
            template="simple_white"
            )
fig.add_shape( # add a horizontal "target" line
    type="line", line_color="black", line_width=3, opacity=1, line_dash="dot",
    x0=0, x1=1, xref="paper", y0=20, y1=20, yref="y"
)




fig.show()


In [29]:
#pie Chart
fig_pie = px.pie(grouped_df, values='value',names='distance_group', title='School students proportion Melbourne and Rest of Victoria',labels={ # replaces default labels by column name
                "distance_group": "Location"})
            #ca)
fig_pie.show()

In [30]:
df = grouped_df
fig_histo = px.histogram(enroll_df, x="distance",nbins=30,color="variable",
                         title="Distribution of Students in schools by their distance from Melbourne CBD",
                         labels={ # replaces default labels by column name
                                 "distance": "Distance from CBD"})
fig_histo.show()

In [31]:
numeric_enroll_df=enroll_df.select_dtypes(include="number")
pearson_corr=numeric_enroll_df.corr()
fig_pearson = px.imshow(pearson_corr, text_auto=True)
fig_pearson.show()

In [32]:
spearman_corr=numeric_enroll_df.corr(method="spearman")
fig_spearman = px.imshow(spearman_corr, text_auto=True)
fig_spearman.show()

In [39]:
#pandas_profiling
!pip install pandas-profiling[notebook]
profile = ProfileReport(enroll_df)
profile
#new_test_haver_1=new_test_haversine.dropna()
#new_test_haver_1['distance']=haversine_vector(new_test_haver_1['X'],new_test_haver_1['Y'], Unit.KILOMETERS)
#new_test_haver_1['distance']=new_test_haver_1.apply(lambda h: haversine((h['X'],h['Y']),unit=Unit.KILOMETERS))

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


Exception ignored in: 'pandas._libs.index.IndexEngine._call_map_locations'
Traceback (most recent call last):
  File "pandas/_libs/hashtable_class_helper.pxi", line 5231, in pandas._libs.hashtable.PyObjectHashTable.map_locations
TypeError: unhashable type: 'Point'


TypeError: ignored

In [34]:
#dtale visualising dataset
dtale_file=dtale.show(merged_enroll)
dtale_file.open_browser()

In [35]:
#Geopandas
gdf = gpd.GeoDataFrame(
    enroll_df, geometry=gpd.points_from_xy(enroll_df.X, enroll_df.Y))

In [36]:
#folium Map
from folium import plugins
gdf_cbd=gdf.query('Address_Postcode<=3025.0')
map_school=folium.Map(location=[-37.8136, 144.9631],tiles='Cartodb dark_matter',zoom_start=12)
#fig3.add_child(m3)
incidents = folium.map.FeatureGroup()
for lat, lng, in zip(gdf_cbd.Y, gdf_cbd.X):
    incidents.add_child(
        folium.CircleMarker(
            [lat, lng],
            radius=5,
            color='yellow',
            fill=True,
            fill_color='blue',
            fill_opacity=0.6
))
labels = list(gdf_cbd.School_Name)
for lat, lng, label in zip(gdf_cbd.Y, gdf_cbd.X, labels):
    folium.Marker([lat,lng], popup=label).add_to(map_school)
map_school.add_child(incidents)
map_school

In [37]:
#gdf_cbd.head()
world = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres'))

# We restrict to South America.
ax = world[world.continent == 'Oceania'].plot(
    color='white', edgecolor='black')
plt.show()

SyntaxError: ignored